In [1]:
import random
import tqdm, tqdm.notebook

from pathlib import Path
from hloc import extract_features, match_features, reconstruction, visualization, pairs_from_exhaustive
from hloc.visualization import plot_images, read_image
from hloc.utils import viz_3d

tqdm.tqdm = tqdm.notebook.tqdm

In [2]:
# Set configurations
image_dir = Path('datasets/digger/images')
outputs = Path('outputs/tractor/')
sfm_pairs = outputs / 'pairs-sfm.txt'
loc_pairs = outputs / 'pairs-loc.txt'
sfm_full_dir = outputs / 'sfm_full'
sfm_dir = outputs / 'sfm'
features = outputs / 'features.h5'
matches = outputs / 'matches.h5'
feature_conf = extract_features.confs['superpoint_aachen']
matcher_conf = match_features.confs['superglue']

# Load image paths
images = [str(p.relative_to(image_dir)) for p in image_dir.iterdir()]
train = random.sample(images, int(0.3 * len(images)))
test = [i for i in images if i not in train]

In [4]:
# SfM on all images
extract_features.main(feature_conf, image_dir, image_list=images, feature_path=features)
pairs_from_exhaustive.main(sfm_pairs, image_list=images)
match_features.main(matcher_conf, sfm_pairs, features=features, matches=matches)
full_model = reconstruction.main(sfm_dir, image_dir, sfm_pairs, features, matches, image_list=images)

[2022/05/17 18:04:34 hloc INFO] Extracting local features with configuration:
{'model': {'max_keypoints': 4096, 'name': 'superpoint', 'nms_radius': 3},
 'output': 'feats-superpoint-n4096-r1024',
 'preprocessing': {'grayscale': True, 'resize_max': 1024}}
[2022/05/17 18:04:34 hloc INFO] Skipping the extraction.
[2022/05/17 18:04:34 hloc INFO] Found 11781 pairs.
[2022/05/17 18:04:34 hloc INFO] Matching local features with configuration:
{'model': {'name': 'superglue',
           'sinkhorn_iterations': 50,
           'weights': 'outdoor'},
 'output': 'matches-superglue'}
[2022/05/17 18:04:34 hloc INFO] Skipping the matching.
[2022/05/17 18:04:34 hloc INFO] Creating an empty database...
[2022/05/17 18:04:34 hloc INFO] Importing images into the database...
[2022/05/17 18:05:16 hloc INFO] Importing features into the database...
100%|████████████████████████████████████████████████████████████| 154/154 [00:00<00:00, 1553.31it/s]
[2022/05/17 18:05:16 hloc INFO] Importing matches into the databa

In [13]:
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, full_model, color='rgba(255,0,0,0.5)', name="full model")
fig.show()

In [7]:
# SfM on training set
extract_features.main(feature_conf, image_dir, image_list=train, feature_path=features)
pairs_from_exhaustive.main(sfm_pairs, image_list=train)
match_features.main(matcher_conf, sfm_pairs, features=features, matches=matches)
small_model = reconstruction.main(sfm_full_dir, image_dir, sfm_pairs, features, matches, image_list=train)

[2022/05/17 19:06:04 hloc INFO] Extracting local features with configuration:
{'model': {'max_keypoints': 4096, 'name': 'superpoint', 'nms_radius': 3},
 'output': 'feats-superpoint-n4096-r1024',
 'preprocessing': {'grayscale': True, 'resize_max': 1024}}
[2022/05/17 19:06:04 hloc INFO] Skipping the extraction.
[2022/05/17 19:06:04 hloc INFO] Found 1035 pairs.
[2022/05/17 19:06:04 hloc INFO] Matching local features with configuration:
{'model': {'name': 'superglue',
           'sinkhorn_iterations': 50,
           'weights': 'outdoor'},
 'output': 'matches-superglue'}
[2022/05/17 19:06:04 hloc INFO] Skipping the matching.
[2022/05/17 19:06:04 hloc INFO] Creating an empty database...
[2022/05/17 19:06:04 hloc INFO] Importing images into the database...
[2022/05/17 19:06:17 hloc INFO] Importing features into the database...
100%|████████████████████████████████████████████████████████████████████████████████████████████████| 46/46 [00:00<00:00, 1464.78it/s]
[2022/05/17 19:06:17 hloc INFO] 

In [12]:
fig_1 = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig_1, small_model, color='rgba(255,0,0,0.5)', name="small model")
fig_1.show()

In [17]:
references_registered = [small_model.images[i].name for i in small_model.reg_image_ids()]
extract_features.main(feature_conf, image_dir, image_list=test, feature_path=features, overwrite=True)
pairs_from_exhaustive.main(loc_pairs, image_list=test, ref_list=references_registered)
match_features.main(matcher_conf, loc_pairs, features=features, matches=matches, overwrite=True);

[2022/05/17 20:34:16 hloc INFO] Extracting local features with configuration:
{'model': {'max_keypoints': 4096, 'name': 'superpoint', 'nms_radius': 3},
 'output': 'feats-superpoint-n4096-r1024',
 'preprocessing': {'grayscale': True, 'resize_max': 1024}}


Loaded SuperPoint model


100%|████████████████████████████████████████████████████████████████████████████████████████████████| 108/108 [00:24<00:00,  4.41it/s]
[2022/05/17 20:34:41 hloc INFO] Finished exporting features.
[2022/05/17 20:34:41 hloc INFO] Found 4968 pairs.
[2022/05/17 20:34:41 hloc INFO] Matching local features with configuration:
{'model': {'name': 'superglue',
           'sinkhorn_iterations': 50,
           'weights': 'outdoor'},
 'output': 'matches-superglue'}


Loaded SuperGlue model ("outdoor" weights)


100%|██████████████████████████████████████████████████████████████████████████████████████████████| 4968/4968 [05:55<00:00, 13.99it/s]
[2022/05/17 20:40:36 hloc INFO] Finished exporting matches.


In [32]:
import pycolmap
from hloc.localize_sfm import QueryLocalizer, pose_from_cluster
conf = {
    'estimation': {'ransac': {'max_error': 12}},
    'refinement': {'refine_focal_length': True, 'refine_extra_params': True},
}
localizer = QueryLocalizer(small_model, conf)

for query in test:
    camera = pycolmap.infer_camera_from_image(image_dir / query)
    ref_ids = [small_model.find_image_with_name(n).image_id for n in references_registered]
    ret, log = pose_from_cluster(localizer, query, camera, ref_ids, features, matches)
    pose = pycolmap.Image(tvec=ret['tvec'], qvec=ret['qvec'])
    viz_3d.plot_camera_colmap(fig_1, pose, camera, color='rgba(0,255,0,0.5)', name=query)

In [33]:
fig_1.show()